In [97]:
import numpy as np 
import pandas as pd 
from datetime import date

In [98]:
ratios = [0,0.236, 0.382, 0.5 , 0.618, 0.786,1,1.414,1.618]
fiblevels = np.array(ratios)

In [99]:
def RSI(series, period=14):
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    return 100 - 100 / (1 + rs)


# calculating Stoch RSI (gives the same values as TradingView)
# https://www.tradingview.com/wiki/Stochastic_RSI_(STOCH_RSI) 
def STRSIA(series, period=14, smoothK=3, smoothD=3):
    # Calculate RSI 
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    rsi = 100 - 100 / (1 + rs)

    # Calculate StochRSI 
    stochrsi  = (rsi - rsi.rolling(period).min()) / (rsi.rolling(period).max() - rsi.rolling(period).min())
    stochrsi_K = stochrsi.rolling(smoothK).mean()
    stochrsi_D = stochrsi_K.rolling(smoothD).mean()
    return stochrsi, stochrsi_K, stochrsi_D

In [100]:
ratios

[0, 0.236, 0.382, 0.5, 0.618, 0.786, 1, 1.414, 1.618]

In [101]:
ada15 = pd.read_json('BN-main/ETH_USDT-1h.json')
ada15

0        1        2        3        4            5
0     1609459200000   736.42   739.00   729.33   734.07  27932.69884
1     1609462800000   734.08   749.00   733.37   748.28  52336.18779
2     1609466400000   748.27   749.00   742.27   744.06  33019.50100
3     1609470000000   744.06   747.23   743.10   744.82  17604.80859
4     1609473600000   744.87   747.09   739.30   742.29  18794.15424
...             ...      ...      ...      ...      ...          ...
4653  1626235200000  1884.21  1898.00  1878.13  1891.01  20544.18102
4654  1626238800000  1891.01  1895.40  1868.19  1873.51  23605.61026
4655  1626242400000  1873.53  1889.69  1865.31  1876.99  25588.05760
4656  1626246000000  1876.99  1906.88  1875.94  1899.70  27277.13934
4657  1626249600000  1899.70  1904.37  1875.56  1878.38  23663.64156

[4658 rows x 6 columns]

In [102]:
ada15.columns=['date','open','high','low','close','volume']
ada15

date     open     high      low    close       volume
0     1609459200000   736.42   739.00   729.33   734.07  27932.69884
1     1609462800000   734.08   749.00   733.37   748.28  52336.18779
2     1609466400000   748.27   749.00   742.27   744.06  33019.50100
3     1609470000000   744.06   747.23   743.10   744.82  17604.80859
4     1609473600000   744.87   747.09   739.30   742.29  18794.15424
...             ...      ...      ...      ...      ...          ...
4653  1626235200000  1884.21  1898.00  1878.13  1891.01  20544.18102
4654  1626238800000  1891.01  1895.40  1868.19  1873.51  23605.61026
4655  1626242400000  1873.53  1889.69  1865.31  1876.99  25588.05760
4656  1626246000000  1876.99  1906.88  1875.94  1899.70  27277.13934
4657  1626249600000  1899.70  1904.37  1875.56  1878.38  23663.64156

[4658 rows x 6 columns]

In [103]:
start = pd.to_datetime('2020-01-01')
ada15.date=pd.to_datetime(ada15['date'],unit='ms')
ada15


date     open     high      low    close       volume
0    2021-01-01 00:00:00   736.42   739.00   729.33   734.07  27932.69884
1    2021-01-01 01:00:00   734.08   749.00   733.37   748.28  52336.18779
2    2021-01-01 02:00:00   748.27   749.00   742.27   744.06  33019.50100
3    2021-01-01 03:00:00   744.06   747.23   743.10   744.82  17604.80859
4    2021-01-01 04:00:00   744.87   747.09   739.30   742.29  18794.15424
...                  ...      ...      ...      ...      ...          ...
4653 2021-07-14 04:00:00  1884.21  1898.00  1878.13  1891.01  20544.18102
4654 2021-07-14 05:00:00  1891.01  1895.40  1868.19  1873.51  23605.61026
4655 2021-07-14 06:00:00  1873.53  1889.69  1865.31  1876.99  25588.05760
4656 2021-07-14 07:00:00  1876.99  1906.88  1875.94  1899.70  27277.13934
4657 2021-07-14 08:00:00  1899.70  1904.37  1875.56  1878.38  23663.64156

[4658 rows x 6 columns]

In [104]:
start = pd.to_datetime('2021-04-01')
end = pd.to_datetime('2021-05-30')


ada2021 = ada15.loc[(ada15['date']> start)& (ada15['date']< end)].copy()
ada2021['RSI'] = RSI(ada2021['close'])
ada2021['RSI4']=RSI(ada2021['close'],56)
ada2021['RSI8']=RSI(ada2021['close'],112)
ada2021['STRSI'] = STRSIA(ada2021['close'])[0]
ada2021['STRSIK'] = STRSIA(ada2021['close'])[1]
ada2021['STRSID'] = STRSIA(ada2021['close'])[2]

ada2021['STRSI4'] = STRSIA(ada2021['close'],56,12,12)[0]
ada2021['STRSIK4'] = STRSIA(ada2021['close'],56,12,12)[1]
ada2021['STRSID4'] = STRSIA(ada2021['close'],56,12,12)[2]

ada2021['STRSI8'] = STRSIA(ada2021['close'],112,24,24)[0]
ada2021['STRSIK8'] = STRSIA(ada2021['close'],112,24,24)[1]
ada2021['STRSID8'] = STRSIA(ada2021['close'],112,24,24)[2]



ada2021

date     open     high      low    close       volume  \
2159 2021-04-01 01:00:00  1932.37  1944.00  1923.61  1939.81  21968.95991   
2160 2021-04-01 02:00:00  1940.00  1944.66  1924.29  1925.40  24216.36219   
2161 2021-04-01 03:00:00  1925.34  1926.00  1912.64  1922.80  24068.29736   
2162 2021-04-01 04:00:00  1923.04  1928.48  1899.88  1915.92  29712.77096   
2163 2021-04-01 05:00:00  1916.22  1920.67  1902.91  1909.12  20097.21333   
...                  ...      ...      ...      ...      ...          ...   
3564 2021-05-29 19:00:00  2273.00  2286.27  2216.60  2247.04  63224.95665   
3565 2021-05-29 20:00:00  2247.09  2272.96  2204.10  2236.94  79891.20893   
3566 2021-05-29 21:00:00  2236.95  2280.51  2223.72  2278.98  40836.89882   
3567 2021-05-29 22:00:00  2278.76  2289.43  2252.16  2272.04  39249.33861   
3568 2021-05-29 23:00:00  2272.05  2323.23  2244.27  2278.74  57534.24537   

            RSI       RSI4       RSI8     STRSI    STRSIK    STRSID    STRSI4  \
2159        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2160        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2161        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2162        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2163        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
...         ...        ...        ...       ...       ...       ...       ...   
3564  31.287914  42.791303  45.719145  0.000000  0.008677  0.084013  0.000000   
3565  30.633117  42.589968  45.622558  0.000000  0.008677  0.047791  0.000000   
3566  36.582422  43.712361  46.100788  0.448194  0.149398  0.055584  0.096401   
3567  36.033012  43.569189  46.033354  0.406804  0.285000  0.147692  0.090896   
3568  37.016459  43.750287  46.110142  0.480893  0.445297  0.293232  0.111655   

       STRSIK4   STRSID4    STRSI8   STRSIK8   STRSID8  
2159       NaN       NaN       NaN       NaN       NaN  
2160       NaN       NaN       NaN       NaN       NaN  
2161       NaN       NaN       NaN       NaN       NaN  
2162       NaN       NaN       NaN       NaN       NaN  
2163       NaN       NaN       NaN       NaN       NaN  
...        ...       ...       ...       ...       ...  
3564  0.106468  0.213408  0.000000  0.211259  0.435172  
3565  0.087088  0.200921  0.000000  0.194605  0.415693  
3566  0.078498  0.186332  0.082126  0.186704  0.396963  
3567  0.072178  0.170349  0.070545  0.179336  0.379008  
3568  0.061154  0.152394  0.083732  0.170830  0.361687  

[1410 rows x 18 columns]

In [105]:
#maxlevels = [13,13,13,13,13,13,13]
#maxlevels = np.array(maxlevels)
#maxlevels

In [106]:
#minlevels = [11,11,11,11,11,11,11]
#minlevels = np.array(minlevels)
#minlevels

In [107]:
ada2021

date     open     high      low    close       volume  \
2159 2021-04-01 01:00:00  1932.37  1944.00  1923.61  1939.81  21968.95991   
2160 2021-04-01 02:00:00  1940.00  1944.66  1924.29  1925.40  24216.36219   
2161 2021-04-01 03:00:00  1925.34  1926.00  1912.64  1922.80  24068.29736   
2162 2021-04-01 04:00:00  1923.04  1928.48  1899.88  1915.92  29712.77096   
2163 2021-04-01 05:00:00  1916.22  1920.67  1902.91  1909.12  20097.21333   
...                  ...      ...      ...      ...      ...          ...   
3564 2021-05-29 19:00:00  2273.00  2286.27  2216.60  2247.04  63224.95665   
3565 2021-05-29 20:00:00  2247.09  2272.96  2204.10  2236.94  79891.20893   
3566 2021-05-29 21:00:00  2236.95  2280.51  2223.72  2278.98  40836.89882   
3567 2021-05-29 22:00:00  2278.76  2289.43  2252.16  2272.04  39249.33861   
3568 2021-05-29 23:00:00  2272.05  2323.23  2244.27  2278.74  57534.24537   

            RSI       RSI4       RSI8     STRSI    STRSIK    STRSID    STRSI4  \
2159        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2160        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2161        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2162        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
2163        NaN        NaN        NaN       NaN       NaN       NaN       NaN   
...         ...        ...        ...       ...       ...       ...       ...   
3564  31.287914  42.791303  45.719145  0.000000  0.008677  0.084013  0.000000   
3565  30.633117  42.589968  45.622558  0.000000  0.008677  0.047791  0.000000   
3566  36.582422  43.712361  46.100788  0.448194  0.149398  0.055584  0.096401   
3567  36.033012  43.569189  46.033354  0.406804  0.285000  0.147692  0.090896   
3568  37.016459  43.750287  46.110142  0.480893  0.445297  0.293232  0.111655   

       STRSIK4   STRSID4    STRSI8   STRSIK8   STRSID8  
2159       NaN       NaN       NaN       NaN       NaN  
2160       NaN       NaN       NaN       NaN       NaN  
2161       NaN       NaN       NaN       NaN       NaN  
2162       NaN       NaN       NaN       NaN       NaN  
2163       NaN       NaN       NaN       NaN       NaN  
...        ...       ...       ...       ...       ...  
3564  0.106468  0.213408  0.000000  0.211259  0.435172  
3565  0.087088  0.200921  0.000000  0.194605  0.415693  
3566  0.078498  0.186332  0.082126  0.186704  0.396963  
3567  0.072178  0.170349  0.070545  0.179336  0.379008  
3568  0.061154  0.152394  0.083732  0.170830  0.361687  

[1410 rows x 18 columns]

In [108]:
high = ada2021.high
low = ada2021.low
maximums5 = high.rolling(5,5)
max5 = maximums5.max()
minimums5 = low.rolling(5,5)
min5 = minimums5.min()
maximums10 = high.rolling(10,10)
max10 = maximums10.max()
minimums10 = low.rolling(10,10)
min10 = minimums10.min()


In [109]:
len(max5)

1410

In [110]:

ada2021['max5'] = max5
ada2021['max10'] = max10
ada2021['min5'] = min5
ada2021['min10'] = min10

ada2021.tail()

date     open     high      low    close       volume  \
3564 2021-05-29 19:00:00  2273.00  2286.27  2216.60  2247.04  63224.95665   
3565 2021-05-29 20:00:00  2247.09  2272.96  2204.10  2236.94  79891.20893   
3566 2021-05-29 21:00:00  2236.95  2280.51  2223.72  2278.98  40836.89882   
3567 2021-05-29 22:00:00  2278.76  2289.43  2252.16  2272.04  39249.33861   
3568 2021-05-29 23:00:00  2272.05  2323.23  2244.27  2278.74  57534.24537   

            RSI       RSI4       RSI8     STRSI  ...    STRSI4   STRSIK4  \
3564  31.287914  42.791303  45.719145  0.000000  ...  0.000000  0.106468   
3565  30.633117  42.589968  45.622558  0.000000  ...  0.000000  0.087088   
3566  36.582422  43.712361  46.100788  0.448194  ...  0.096401  0.078498   
3567  36.033012  43.569189  46.033354  0.406804  ...  0.090896  0.072178   
3568  37.016459  43.750287  46.110142  0.480893  ...  0.111655  0.061154   

       STRSID4    STRSI8   STRSIK8   STRSID8     max5    max10    min5   min10  
3564  0.213408  0.000000  0.211259  0.435172  2390.02  2466.70  2216.6  2216.6  
3565  0.200921  0.000000  0.194605  0.415693  2390.02  2466.70  2204.1  2204.1  
3566  0.186332  0.082126  0.186704  0.396963  2373.34  2451.52  2204.1  2204.1  
3567  0.170349  0.070545  0.179336  0.379008  2289.54  2425.90  2204.1  2204.1  
3568  0.152394  0.083732  0.170830  0.361687  2323.23  2425.90  2204.1  2204.1  

[5 rows x 22 columns]

In [111]:
#maxnew = np.ones_like(ratios)
#maxnew

In [112]:
#addmin = mintest.tolist()
#addmax = maxtest.tolist()
#data = pd.DataFrame({"max":maxtest,"min":mintest},dtype='float')
#data = data.append(addmin,ignore_index=True)
#data1 = pd.DataFrame(maxtest)
#data2 = pd.DataFrame(mintest)
#data = pd.DataFrame(data1,data2)

In [113]:
#datamul = data.mul([2,1],axis='columns')
#datamul = data['max'].mul(ratios[7])

In [114]:
#datamul

In [115]:
#df = ada2021.loc[(ada2021['max10']>0)& (ada2021['min10']>0)]
df = ada2021
#len(df['date'])
average = df['max5']-df['min5']
avg = average.mean()
avg
df
#point = df.loc[(df['max5'].diff()>0)]
#pointm = df.loc[(df['min5'].diff()>0)]

df['support5']= df.min5.rolling(5,5).min()
df['support10']= df.min10.rolling(10,10).min()
df['resist5']= df.max5.rolling(5,5).max()
df['resist10']= df.max10.rolling(10,10).max()

#df['RSI'] = RSI(df['close'])
#df['STRSI4']=STRSIA(df['close'],56,12,12)
#df['STRSI8']=STRSIA(df['close'],112,24,24)


point = df[(df['max5'] > df['max5'].shift(1)) &  (df['max5'].shift(1) > df['max5'].shift(2))]
pointm = df[(df['min5'] < df['min5'].shift(1)) &  (df['min5'].shift(1) > df['min5'].shift(2))]
point
#ada2021
pointm

#for row in range(0,len(pointm)):
#    print(pointm['support5'])

date     open     high      low    close        volume  \
2169 2021-04-01 11:00:00  1929.50  1929.67  1906.00  1920.07   30921.81885   
2176 2021-04-01 18:00:00  1940.30  1975.80  1885.02  1967.29   82278.39844   
2182 2021-04-02 00:00:00  1968.05  1972.54  1948.48  1958.16   26775.01634   
2221 2021-04-03 15:00:00  2091.59  2098.08  2069.18  2070.98   44429.54738   
2230 2021-04-04 00:00:00  2008.59  2024.90  1975.24  2001.76   45427.87487   
...                  ...      ...      ...      ...      ...           ...   
3459 2021-05-25 10:00:00  2560.32  2561.49  2378.54  2438.71  178404.93641   
3468 2021-05-25 19:00:00  2576.73  2593.96  2484.62  2512.12   71261.92048   
3483 2021-05-26 10:00:00  2840.98  2855.00  2773.00  2825.47   87788.24406   
3498 2021-05-27 01:00:00  2812.49  2819.00  2666.00  2691.61   88886.51617   
3513 2021-05-27 16:00:00  2803.85  2814.63  2754.44  2765.41   53073.05851   

            RSI       RSI4       RSI8     STRSI  ...   STRSIK8   STRSID8  \
2169        NaN        NaN        NaN       NaN  ...       NaN       NaN   
2176  60.523034        NaN        NaN       NaN  ...       NaN       NaN   
2182  53.227285        NaN        NaN       NaN  ...       NaN       NaN   
2221  47.005130  60.016291        NaN  0.000000  ...       NaN       NaN   
2230  36.245081  52.325817        NaN  0.000000  ...       NaN       NaN   
...         ...        ...        ...       ...  ...       ...       ...   
3459  44.735270  49.211346  47.408351  0.000000  ...  0.937455  0.809150   
3468  49.037247  50.386147  48.149429  0.316780  ...  0.884198  0.895062   
3483  61.913455  55.160759  50.855409  0.402699  ...  0.921550  0.898118   
3498  44.542578  51.583530  49.591995  0.000000  ...  0.926741  0.923882   
3513  49.474697  52.500537  50.241040  0.393579  ...  0.891859  0.908670   

         max5    max10     min5    min10  support5  support10  resist5  \
2169  1967.83  1967.83  1906.00  1899.88   1899.88        NaN  1967.83   
2176  1975.80  1975.80  1885.02  1885.02   1885.02        NaN  1975.80   
2182  1983.36  1984.77  1948.48  1885.02   1885.02    1885.02  1984.77   
2221  2117.80  2130.00  2069.18  2067.28   2067.28    2067.28  2130.00   
2230  2095.44  2098.08  1975.24  1975.24   1975.24    1975.24  2095.69   
...       ...      ...      ...      ...       ...        ...      ...   
3459  2683.65  2737.12  2378.54  2378.54   2378.54    2378.54  2683.65   
3468  2640.02  2650.00  2484.62  2378.54   2382.21    2378.54  2650.00   
3483  2910.00  2910.00  2773.00  2681.58   2754.32    2484.62  2910.00   
3498  2889.74  2889.74  2666.00  2665.56   2665.56    2665.56  2889.74   
3513  2867.96  2867.96  2754.44  2683.93   2683.93    2633.68  2867.96   

      resist10  
2169       NaN  
2176       NaN  
2182   1984.77  
2221   2146.00  
2230   2130.00  
...        ...  
3459   2750.00  
3468   2737.12  
3483   2910.00  
3498   2910.00  
3513   2889.74  

[65 rows x 26 columns]

In [116]:
buypoints = df[(df['STRSI'] < 0.5) &  (df['STRSI4'] < 0.5) & (df['STRSI8'] < 0.5) & (df['close'] <  df['support10'].shift(1)) & (df['RSI']<30)]
sellpoints = df[(df['STRSI'] == 1) &  (df['STRSI4'] == 1) & (df['STRSI8'] == 1)]

#buypoints = df.loc[(df['STRSI'] == 0) &  (df['STRSI4'] == 0) & (df['STRSI8'] == 0)]
buypoints
#sellpoints

date     open     high      low    close        volume  \
2557 2021-04-17 15:00:00  2384.01  2386.34  2330.06  2345.00   50773.51646   
2566 2021-04-18 00:00:00  2317.65  2340.00  2247.49  2283.15   67465.73701   
2569 2021-04-18 03:00:00  2254.30  2268.95  1946.80  2158.90  179459.42213   
3232 2021-05-15 23:00:00  3766.44  3773.37  3632.00  3646.68   54032.64689   
3252 2021-05-16 19:00:00  3474.25  3525.12  3346.72  3419.22  127781.12854   
3260 2021-05-17 03:00:00  3382.14  3399.99  3212.00  3240.13  143851.96194   
3309 2021-05-19 04:00:00  3097.23  3133.18  2858.79  2931.56  232021.83276   
3315 2021-05-19 10:00:00  2973.82  2984.49  2818.88  2856.56  118730.30048   
3316 2021-05-19 11:00:00  2856.66  2866.68  2442.82  2721.08  355439.87786   
3317 2021-05-19 12:00:00  2721.08  2773.52  1960.00  2365.18  437462.36681   
3373 2021-05-21 20:00:00  2349.95  2374.80  2237.00  2247.91  172435.57816   
3409 2021-05-23 08:00:00  2158.01  2158.14  2000.00  2033.84  232921.00957   
3413 2021-05-23 12:00:00  2115.50  2138.27  1900.00  1938.52  209520.75481   
3417 2021-05-23 16:00:00  1924.95  1960.84  1728.74  1848.11  302865.37862   

            RSI       RSI4       RSI8     STRSI  ...   STRSIK8   STRSID8  \
2557  29.248858  48.320657  52.053110  0.000000  ...  0.380005  0.455813   
2566  28.877152  45.229116  49.924984  0.072305  ...  0.256874  0.374430   
2569  18.795547  39.702768  46.391091  0.000000  ...  0.187947  0.348150   
3232  29.630867  44.533499  48.354981  0.000000  ...  0.223268  0.307013   
3252  26.363630  41.403262  46.169668  0.000000  ...  0.107485  0.169686   
3260  28.637302  39.944118  44.854583  0.225371  ...  0.091084  0.130030   
3309  24.298964  39.655009  43.703753  0.000000  ...  0.275394  0.270277   
3315  24.647848  38.975499  43.219432  0.019116  ...  0.187859  0.269918   
3316  20.386523  37.198364  42.160398  0.000000  ...  0.170102  0.266652   
3317  13.690444  33.154891  39.589089  0.000000  ...  0.157252  0.262706   
3373  28.782974  40.041118  42.585090  0.000000  ...  0.584233  0.558402   
3409  28.273528  39.857474  42.337521  0.000000  ...  0.507597  0.485226   
3413  28.356476  39.115746  41.873807  0.004237  ...  0.478456  0.487305   
3417  26.540561  38.211134  41.352712  0.000000  ...  0.440477  0.484667   

         max5    max10     min5    min10  support5  support10  resist5  \
2557  2429.43  2481.89  2330.06  2330.06   2330.06    2330.06  2475.65   
2566  2395.54  2395.54  2247.49  2247.49   2247.49    2247.49  2395.54   
2569  2383.54  2395.54  1946.80  1946.80   1946.80    1946.80  2395.54   
3232  3831.00  3921.06  3632.00  3632.00   3632.00    3632.00  3921.06   
3252  3691.62  3860.66  3346.72  3346.72   3346.72    3346.72  3849.76   
3260  3588.98  3661.00  3212.00  3212.00   3212.00    3212.00  3588.98   
3309  3441.73  3464.02  2858.79  2858.79   2858.79    2858.79  3464.02   
3315  3017.41  3354.90  2818.88  2818.88   2818.88    2818.88  3238.14   
3316  3012.00  3238.14  2442.82  2442.82   2442.82    2442.82  3158.21   
3317  3006.00  3158.21  1960.00  1960.00   1960.00    1960.00  3133.18   
3373  2518.86  2763.09  2237.00  2237.00   2237.00    2237.00  2763.09   
3409  2317.80  2381.57  2000.00  2000.00   2000.00    2000.00  2381.57   
3413  2174.82  2333.90  1900.00  1900.00   1900.00    1900.00  2317.80   
3417  2138.27  2222.05  1728.74  1728.74   1728.74    1728.74  2174.82   

      resist10  
2557   2495.00  
2566   2481.89  
2569   2470.00  
3232   4043.46  
3252   3879.00  
3260   3860.66  
3309   3565.71  
3315   3464.02  
3316   3464.02  
3317   3464.02  
3373   2897.18  
3409   2453.46  
3413   2383.83  
3417   2383.83  

[14 rows x 26 columns]

In [117]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.express as px



#Declare figure


fig = go.Figure()

fig = make_subplots(rows=8, cols=1,subplot_titles=("Price","gap","empty", "RSI 1 4 8", "Stoch 1", "Stoch 4","Stoch 8","Stoch 1 4 8"))
    

    
# buy points     
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['close'],name="buy", mode = "markers+text"), row=1, col=1 
)    

# sell points     
fig.add_trace(
    go.Scatter(x=sellpoints.date, y=sellpoints['close'],name="sell", mode = "markers"), row=1, col=1 
) 
    
# buy points     
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['resist10'],
        name="resist10",
        text="resist10",
        textposition="top center"),
    row=1, col=1
)  
# resistance 10 


fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI'],
        name="RSI",
        text="RSI",
        textposition="top center"),
    row=4, col=1
)

# support 10
fig.add_trace(
    go.Scatter(x=buypoints.date, y=buypoints['support10'],
        name="support10",
        text="support1010",
        textposition="top center"),
    row=1, col=1
)  

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI4'],name="RSI4"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI8'],name="RSI8"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK'],name="STRSIK"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID'],name="STRSID"),
    row=5, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK4'],name="STRSIK4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID4'],name="STRSID4"),
    row=6, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=7, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK8'],name="STRSIK8"),
    row=7, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID8'],name="STRSIK8"),
    row=7, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=8, col=1
)


#add Traces

fig.add_trace(go.Candlestick(x=df.date,
                open=df['open'],
                high=df['high'],
                low=df['low'],
                close=df['close'], name = 'market data'),row=1,col=1)

#fig.add_trace(go.Scatter(x=df['date'], y=df['max10']))

#fig.add_trace(go.Scatter(x=df['date'], y=df['min10']))

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist5']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support5']))


#fig.add_shape(type="line",
#    x0=pointm['date'], y0=pointm['support5'], x1=max(pointm['date']), y1=pointm['support5'],
#    line=dict(
#        color="LightSeaGreen",
#        width=4,
#        dash="dashdot",
#    ))
fig.update_shapes(dict(xref='x', yref='y'))

#for index in range(0,len(pointm)):
    #fig.add_hline(y=pointm['support5'])

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist10']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support10']))
#for i in range(len(df['date'])):
    #fig.add_hline(y=df[i]['min10'], line_dash="dot",
                  #annotation_text="support", 
                  #annotation_position="bottom right")

#fig.add_hline(y=df['max10'], line_dash="dot",
#              annotation_text="resitance", 
#              annotation_position="bottom right")



fig.update_layout(height=3000, width=800, title_text="top sub plots")
# X and Y Axis Update
fig.update_xaxes(
    title = 'Date',rangeslider_visible=False
)

#fig.update_yaxes(
#    title = 'Share Price (USD)'
#)

#Show
fig.show()

In [71]:
import plotly.graph_objs as go

import plotly.express as px
import pandas as pd


px.scatter(x=buypoints.date, y=buypoints['close'])



fig.show()